In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
!pip install neuralprophet
!pip install git+https://github.com/ourownstory/neural_prophet.git numpy==1.23.5

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 145.4/145.4 kB 4.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 27.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.0/13.0 MB 100.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 829.5/829.5 kB 71.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 841.5/841.5 kB 77.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 345.4/345.4 kB 41.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 23.7/23.7 MB 75.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 823.6/823.6 kB 80.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 14.1/14.1 MB 91.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 731.7/731.7 MB 2.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 410.6/410.6 MB 2.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 121.6/121.6 MB 8.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━

In [ ]:
import pandas as pd
import numpy as np
from neuralprophet import NeuralProphet
import matplotlib.pyplot as plt
import datetime
from sklearn.metrics import mean_absolute_error, mean_squared_error



ERROR:NP.plotly:Importing plotly failed. Interactive plots will not work.
ERROR:NP.plotly:Importing plotly failed. Interactive plots will not work.


# Load historical load and temperature

In [ ]:
def read_ncep_data(filename):
    _df = pd.read_csv(filename,sep=";", skiprows=26, names=col_names)
    _df['Time'] = _df['Time'].replace("24:00", "00:00")

    # Concatenate Date and Time columns
    _df['Datetime'] = _df['Date'] + " " + _df['Time']

    # Convert to datetime type
    _df['Datetime'] = pd.to_datetime(_df['Datetime'])

    # Identify rows where 'Time' is "00:00" and adjust the 'Date' by adding 1 day

    next_day_mask = _df['Time'] == "00:00"
    _df.loc[next_day_mask, 'Datetime'] += pd.DateOffset(days=1)
    _df['Datetime'] = _df['Datetime'] + pd.DateOffset(hours=7)

    dropped_cols = ['Date', 'Time']
    _df.drop(columns=dropped_cols, inplace=True)
    _df.set_index('Datetime', inplace=True)
    return _df

In [ ]:
# read NCEP data
col_names = ['Date', 'Time','Tncep', 'RH', 'Pressure', 'WS', 'WD', 'rain_fall', 'snow_fall', 'snow_depth', 'Incep']


ncep_df_2 = read_ncep_data('/content/drive/MyDrive/neuralprophet/siteCU04_2023-01-01to2023-12-31.csv') #import 2023 data
ncep_df_2['Tncep'] = ncep_df_2['Tncep']-273.5
ncep_df_2['Incep'] = ncep_df_2['Incep'] * 4
ncep_df =ncep_df_2.reset_index()
ncep_df

Datetime  Tncep     RH  Pressure    WS      WD  rain_fall  \
0     2023-01-01 07:15:00  21.01  59.42   1015.53  1.12  348.45        0.0   
1     2023-01-01 07:30:00  21.35  58.39   1015.66  1.23  352.57        0.0   
2     2023-01-01 07:45:00  21.69  57.36   1015.79  1.34  356.02        0.0   
3     2023-01-01 08:00:00  22.04  56.33   1015.92  1.46  358.93        0.0   
4     2023-01-01 08:15:00  22.38  55.30   1016.05  1.58    1.40        0.0   
...                   ...    ...    ...       ...   ...     ...        ...   
35035 2024-01-01 06:00:00  25.17  60.25   1010.75  2.89  332.32        0.0   
35036 2024-01-01 06:15:00  25.11  60.64   1010.83  2.86  333.28        0.0   
35037 2024-01-01 06:30:00  25.06  61.02   1010.91  2.84  334.26        0.0   
35038 2024-01-01 06:45:00  25.00  61.41   1011.00  2.82  335.25        0.0   
35039 2024-01-01 07:00:00  24.94  61.79   1011.08  2.79  336.26        0.0   

       snow_fall  snow_depth     Incep  
0            0.0         0.0   49.2732  
1            0.0         0.0   89.5056  
2            0.0         0.0  135.5892  
3            0.0         0.0  187.1732  
4            0.0         0.0  243.8560  
...          ...         ...       ...  
35035        0.0         0.0    0.0000  
35036        0.0         0.0    0.0000  
35037        0.0         0.0    0.0000  
35038        0.0         0.0    0.0028  
35039        0.0         0.0   18.8516  

[35040 rows x 10 columns]

In [ ]:
load_df = pd.read_csv('/content/drive/MyDrive/neuralprophet/load_data_5minresample_032023_022024.csv', parse_dates=['datetime'],usecols=['datetime','Ptot (kW)'] )
# use only Temp and Incep
ncep_df = ncep_df[['Datetime','Tncep','Incep']]
ncep_df = ncep_df.rename(columns = {'Datetime' : 'datetime'})

In [ ]:
df = pd.DataFrame()
#datetime range of load data
df['datetime'] =  pd.date_range(start = "2023-03-01", end='2023-12-31',freq='5min')
df = df.merge(ncep_df,how='left',on='datetime')
df = df.merge(load_df,how='left',on='datetime')



In [ ]:
df

datetime  Tncep  Incep  Ptot (kW)
0     2023-03-01 00:00:00  26.99    0.0   0.838751
1     2023-03-01 00:05:00    NaN    NaN   0.845447
2     2023-03-01 00:10:00    NaN    NaN   0.895884
3     2023-03-01 00:15:00  26.89    0.0   0.936731
4     2023-03-01 00:20:00    NaN    NaN   0.899579
...                   ...    ...    ...        ...
87836 2023-12-30 23:40:00    NaN    NaN   0.690417
87837 2023-12-30 23:45:00  28.91    0.0   0.680067
87838 2023-12-30 23:50:00    NaN    NaN   0.695497
87839 2023-12-30 23:55:00    NaN    NaN   0.811797
87840 2023-12-31 00:00:00  28.78    0.0   0.633348

[87841 rows x 4 columns]

In [ ]:
# impute missing load by using same day in a week before
df.loc[(df['datetime']>= '2023-04-05') & (df['datetime'] <= '2023-04-06'),'Ptot (kW)'] = df[(df['datetime']>= '2023-03-28') & (df['datetime'] <= '2023-03-29')]['Ptot (kW)'].values
df.loc[(df['datetime']>= '2023-07-11') & (df['datetime'] <= '2023-07-13'),'Ptot (kW)'] = df[(df['datetime']>= '2023-07-04') & (df['datetime'] <= '2023-07-06')]['Ptot (kW)'].values

In [ ]:
df

datetime  Tncep  Incep  Ptot (kW)
0     2023-03-01 00:00:00  26.99    0.0   0.838751
1     2023-03-01 00:05:00    NaN    NaN   0.845447
2     2023-03-01 00:10:00    NaN    NaN   0.895884
3     2023-03-01 00:15:00  26.89    0.0   0.936731
4     2023-03-01 00:20:00    NaN    NaN   0.899579
...                   ...    ...    ...        ...
87836 2023-12-30 23:40:00    NaN    NaN   0.690417
87837 2023-12-30 23:45:00  28.91    0.0   0.680067
87838 2023-12-30 23:50:00    NaN    NaN   0.695497
87839 2023-12-30 23:55:00    NaN    NaN   0.811797
87840 2023-12-31 00:00:00  28.78    0.0   0.633348

[87841 rows x 4 columns]

In [ ]:
#check if missing load has been imputed
import plotly.graph_objects as go
import plotly.express as px
#df_ecal = df.loc[(df['datetime']>= '2023-04-05') & (df['datetime'] <= '2023-04-06')]
df_ecal = df.loc[(df['datetime']>= '2023-07-11') & (df['datetime'] <= '2023-07-13')]
fig = px.line(df_ecal, x=df_ecal['datetime'],  y=['Ptot (kW)'])
fig.show()

WARNING - (py.warnings._showwarnmsg) - /usr/local/lib/python3.10/dist-packages/_plotly_utils/basevalidators.py:105: FutureWarning: The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result
  v = v.dt.to_pydatetime()

  v = v.dt.to_pydatetime()



# Add lab machine schedule as  0 1 variable
## lab day 0 no lab 1 have lab
## lab hour using that hour as value i.e. 13:00, 13:45 -> 13 14:10,14:15 -> 14

In [ ]:
df['lab_hour'] = 0
df['lab_day'] = 0
machine_lab_day_list = ['2023-01-16', #w2
                '2023-01-23', #w3
                '2023-01-30', #w4
                '2023-02-13', #w6
                '2023-02-20', #w7
                '2023-02-27', #w8
                '2023-03-20', #w11
                '2023-03-27', #w12
                '2023-04-03', #w13
                '2023-04-24', #w16
                '2023-05-01'  #w17
                ] #only Monday of lab weeks
machine_lab_day_list = [(datetime.datetime.strptime(day,'%Y-%m-%d'),datetime.datetime.strptime(day,'%Y-%m-%d') + datetime.timedelta(days=4)) for day in machine_lab_day_list] #full lab schedule
power_lab_day_list = [ '2023-01-20', #w2
                                  '2023-01-27', #w3
                                  '2023-02-10',#w5
                                  '2023-02-17',#w6
                                  '2023-02-24',#w7
                                  '2023-03-17',#w10
                                  '2023-03-24',#w11
                                  '2023-03-31',#w12
                                  '2023-04-07',#w13
                                  '2023-04-21' #w15
                        ] #Power lab is only on Friday
power_lab_day_list = [(datetime.datetime.strptime(day,'%Y-%m-%d'),datetime.datetime.strptime(day,'%Y-%m-%d') + datetime.timedelta(days=1)) for day in power_lab_day_list]
for start,end in machine_lab_day_list :
    df.loc[(df['datetime'] >= start) & (df['datetime'] <= end),'lab_day' ] = 1
    for i in range(4) :
        #assume lab preparation time is @ 13:00 and lab is ending @ 17:00
        df.loc[(df['datetime'] >= start + datetime.timedelta(days=i,hours=13))
               & (df['datetime'] <= start + datetime.timedelta(days=i,hours=17) ),'lab_hour' ] = df.loc[(df['datetime'] >= start + datetime.timedelta(days=i,hours=13))
                                                                                                                                            & (df['datetime'] <= start + datetime.timedelta(days=i,hours=17) ),'datetime' ].dt.hour
for start,end in power_lab_day_list :
    df.loc[(df['datetime'] >= start) & (df['datetime'] <= end),'lab_day' ] = 1
    df.loc[(df['datetime'] >= start + datetime.timedelta(hours=13))
               & (df['datetime'] <= start + datetime.timedelta(hours=17) ),'lab_hour' ] = df.loc[(df['datetime'] >= start + datetime.timedelta(hours=13))
                                                                                                                                          & (df['datetime'] <= start + datetime.timedelta(hours=17) ),'datetime' ].dt.hour

In [ ]:
#impute minor missing
df = df.set_index('datetime').interpolate(method='linear', axis=0)
df

Tncep  Incep  Ptot (kW)  lab_hour  lab_day
datetime                                                           
2023-03-01 00:00:00  26.990000    0.0   0.838751         0        1
2023-03-01 00:05:00  26.956667    0.0   0.845447         0        1
2023-03-01 00:10:00  26.923333    0.0   0.895884         0        1
2023-03-01 00:15:00  26.890000    0.0   0.936731         0        1
2023-03-01 00:20:00  26.856667    0.0   0.899579         0        1
...                        ...    ...        ...       ...      ...
2023-12-30 23:40:00  28.956667    0.0   0.690417         0        0
2023-12-30 23:45:00  28.910000    0.0   0.680067         0        0
2023-12-30 23:50:00  28.866667    0.0   0.695497         0        0
2023-12-30 23:55:00  28.823333    0.0   0.811797         0        0
2023-12-31 00:00:00  28.780000    0.0   0.633348         0        0

[87841 rows x 5 columns]

# Train test split

In [ ]:
prophet_df = pd.DataFrame({'ds':df.index,
                           'y' : df['Ptot (kW)'],
                           'Tncep'	: df['Tncep'],
                           'Incep'	: df['Incep'],
                           'lab_hour' : df['lab_hour'],
                           'lab_day' : df['lab_day']
                           })

In [ ]:
#check if missing load has been imputed
import plotly.graph_objects as go
import plotly.express as px
#df_ecal = df.loc[(df['datetime']>= '2023-04-05') & (df['datetime'] <= '2023-04-06')]
df_ecal = prophet_df
fig = px.line(df_ecal, x=df_ecal.index,  y=['Tncep'])
fig.show()

WARNING - (py.warnings._showwarnmsg) - /usr/local/lib/python3.10/dist-packages/_plotly_utils/basevalidators.py:105: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result




In [ ]:
# split_idx = (prophet_df.shape[0]*1)//5
# train_data = prophet_df.iloc[split_idx:,:] # 80:20 train:test
# test_data = prophet_df.iloc[:split_idx,:]
train_data = prophet_df.iloc[:(prophet_df.shape[0]*4)//5,:] # 80:20 train:test
test_data = prophet_df.iloc[(prophet_df.shape[0]*4)//5:,:]

In [ ]:
train_data

ds         y      Tncep  Incep  lab_hour  \
datetime                                                                        
2023-03-01 00:00:00 2023-03-01 00:00:00  0.838751  26.990000    0.0         0   
2023-03-01 00:05:00 2023-03-01 00:05:00  0.845447  26.956667    0.0         0   
2023-03-01 00:10:00 2023-03-01 00:10:00  0.895884  26.923333    0.0         0   
2023-03-01 00:15:00 2023-03-01 00:15:00  0.936731  26.890000    0.0         0   
2023-03-01 00:20:00 2023-03-01 00:20:00  0.899579  26.856667    0.0         0   
...                                 ...       ...        ...    ...       ...   
2023-10-30 23:35:00 2023-10-30 23:35:00  1.901280  25.016667    0.0         0   
2023-10-30 23:40:00 2023-10-30 23:40:00  2.218596  24.983333    0.0         0   
2023-10-30 23:45:00 2023-10-30 23:45:00  2.546513  24.950000    0.0         0   
2023-10-30 23:50:00 2023-10-30 23:50:00  1.923745  24.913333    0.0         0   
2023-10-30 23:55:00 2023-10-30 23:55:00  2.600186  24.876667    0.0         0   

                     lab_day  
datetime                      
2023-03-01 00:00:00        1  
2023-03-01 00:05:00        1  
2023-03-01 00:10:00        1  
2023-03-01 00:15:00        1  
2023-03-01 00:20:00        1  
...                      ...  
2023-10-30 23:35:00        0  
2023-10-30 23:40:00        0  
2023-10-30 23:45:00        0  
2023-10-30 23:50:00        0  
2023-10-30 23:55:00        0  

[70272 rows x 6 columns]

In [ ]:
nnProphet_model = NeuralProphet(
    yearly_seasonality=False,  # Turn off yearly seasonality (data has only 03-2023 to 08-2023)
    weekly_seasonality=True,  # Turn on weekly seasonality (load may have weekly pattern)
    daily_seasonality=True,  # Enable daily seasonality load may have daily patterns
    n_forecasts=12, # 60 min ahead (5 min resolution)
    n_lags=12, # 60 min lag (5 min resolution)
    impute_missing=True

    )

#if future regress need temp solar predict
nnProphet_model.add_future_regressor('Tncep')
nnProphet_model.add_future_regressor('Incep')
nnProphet_model.add_future_regressor('lab_hour')
nnProphet_model.add_future_regressor('lab_day')   #change to future reg
learning_rate = 0.01  # Set an initial learning rate

# Training the model with manual learning rate adjustment
metrics = nnProphet_model.fit(train_data, freq="5T", learning_rate=learning_rate)

WARNING - (NP.forecaster.fit) - When Global modeling with local normalization, metrics are displayed in normalized scale.
WARNING - (py.warnings._showwarnmsg) - /usr/local/lib/python3.10/dist-packages/neuralprophet/df_utils.py:1152: FutureWarning:

Series.view is deprecated and will be removed in a future version. Use ``astype`` as an alternative to change the dtype.



Series.view is deprecated and will be removed in a future version. Use ``astype`` as an alternative to change the dtype.


INFO - (NP.df_utils._infer_frequency) - Major frequency 5min corresponds to 99.999% of the data.
INFO:NP.df_utils:Major frequency 5min corresponds to 99.999% of the data.
WARNING - (py.warnings._showwarnmsg) - /usr/local/lib/python3.10/dist-packages/neuralprophet/df_utils.py:1173: FutureWarning:

'T' is deprecated and will be removed in a future version, please use 'min' instead.



'T' is deprecated and will be removed in a future version, please use 'min' instead.


WARNING - (py.warnings._showwar

Training: 0it [00:00, ?it/s]

In [ ]:
# raw true based on forecast start
# default based on datetime target
#forecast = nnProphet_model.predict(test_data,raw = True)
forecast = nnProphet_model.predict(prophet_df,raw = True)
forecast = forecast.dropna()
forecast

WARNING - (NP.forecaster.predict) - Raw forecasts are incompatible with plotting utilities
WARNING - (py.warnings._showwarnmsg) - /usr/local/lib/python3.10/dist-packages/neuralprophet/df_utils.py:1152: FutureWarning:

Series.view is deprecated and will be removed in a future version. Use ``astype`` as an alternative to change the dtype.



Series.view is deprecated and will be removed in a future version. Use ``astype`` as an alternative to change the dtype.


INFO - (NP.df_utils._infer_frequency) - Major frequency 5min corresponds to 99.999% of the data.
INFO:NP.df_utils:Major frequency 5min corresponds to 99.999% of the data.
WARNING - (py.warnings._showwarnmsg) - /usr/local/lib/python3.10/dist-packages/neuralprophet/df_utils.py:1173: FutureWarning:

'T' is deprecated and will be removed in a future version, please use 'min' instead.



'T' is deprecated and will be removed in a future version, please use 'min' instead.


WARNING - (py.warnings._showwarnmsg) - /usr/local/lib/python3.

Predicting: 275it [00:00, ?it/s]

INFO - (NP.df_utils.return_df_in_original_format) - Returning df with no ID column
INFO:NP.df_utils:Returning df with no ID column


ds     step0    trend0  season_weekly0  season_daily0  \
0     2023-03-01 01:00:00  1.048114  9.134590        0.838072      -2.006818   
1     2023-03-01 01:05:00  0.979727  9.134403        0.834585      -2.011871   
2     2023-03-01 01:10:00  0.947180  9.134216        0.831737      -2.012483   
3     2023-03-01 01:15:00  0.920511  9.134028        0.828286      -2.012497   
4     2023-03-01 01:20:00  0.923172  9.133842        0.827665      -2.012795   
...                   ...       ...       ...             ...            ...   
87812 2023-12-30 22:40:00  0.701860  6.428277       -2.398762      -1.068174   
87813 2023-12-30 22:45:00  0.653064  6.428370       -2.398263      -1.146978   
87814 2023-12-30 22:50:00  0.653528  6.428462       -2.397057      -1.201471   
87815 2023-12-30 22:55:00  0.712715  6.428554       -2.396425      -1.257680   
87816 2023-12-30 23:00:00  0.680692  6.428647       -2.395774      -1.312359   

            ar0  future_regressors_additive0  future_regressor_Incep0  \
0     -6.043131                    -0.874597                      0.0   
1     -6.110330                    -0.867059                      0.0   
2     -6.146769                    -0.859521                      0.0   
3     -6.177323                    -0.851983                      0.0   
4     -6.181094                    -0.844444                      0.0   
...         ...                          ...                      ...   
87812 -1.317205                    -0.942277                      0.0   
87813 -1.294789                    -0.935277                      0.0   
87814 -1.248667                    -0.927739                      0.0   
87815 -1.141533                    -0.920200                      0.0   
87816 -1.127159                    -0.912662                      0.0   

       future_regressor_Tncep0  future_regressor_lab_day0  ...    step11  \
0                    -0.471677                   -0.40292  ...  2.105281   
1                    -0.464139                   -0.40292  ...  2.053452   
2                    -0.456600                   -0.40292  ...  2.015635   
3                    -0.449062                   -0.40292  ...  1.979300   
4                    -0.441524                   -0.40292  ...  1.995581   
...                        ...                        ...  ...       ...   
87812                -0.942277                    0.00000  ...  0.449611   
87813                -0.935277                    0.00000  ...  0.430647   
87814                -0.927739                    0.00000  ...  0.446640   
87815                -0.920200                    0.00000  ...  0.522165   
87816                -0.912662                    0.00000  ...  0.493192   

        trend11  season_weekly11  season_daily11      ar11  \
0      9.132531         0.807363       -2.013879 -5.030134   
1      9.132344         0.806015       -2.017200 -5.085183   
2      9.132156         0.800761       -2.025212 -5.117086   
3      9.131969         0.799434       -2.028637 -5.156019   
4      9.131783         0.796796       -2.038829 -5.134260   
...         ...              ...             ...       ...   
87812  6.429291        -2.389206       -1.638693 -1.088655   
87813  6.429383        -2.387847       -1.680396 -1.074907   
87814  6.429475        -2.386689       -1.719335 -1.028762   
87815  6.429566        -2.386083       -1.743891 -0.936379   
87816  6.429660        -2.384318       -1.785418 -0.932683   

       future_regressors_additive11  future_regressor_Incep11  \
0                         -0.790600                       0.0   
1                         -0.782523                       0.0   
2                         -0.774985                       0.0   
3                         -0.767447                       0.0   
4                         -0.759909                       0.0   
...                             ...                       ...   
87812                     -0.863125                       0.0   
87813  

In [ ]:
#forecast.to_csv('load_NearRT_20231031_20231230.csv',index=False)
forecast[['ds'+'y']+ [f'yhat{i+1}' for i in range(12)]].to_csv('load_NearRT_20230301_20231230.csv',index=False)

In [ ]:
import pandas as pd
import numpy as np
#from neuralprophet import NeuralProphet
import matplotlib.pyplot as plt
import datetime
from sklearn.metrics import mean_absolute_error, mean_squared_error
import plotly.graph_objects as go
import plotly.express as px


In [ ]:
forecast = pd.read_csv('/content/drive/MyDrive/data for senior prj/load_NearRT_20231031_20231230.csv',parse_dates=['ds'])
forecast

ds         y     yhat1     yhat2     yhat3     yhat4  \
0     2023-10-31 01:55:00  0.514536  0.494525  0.470645  0.471113  0.477749   
1     2023-10-31 02:00:00  0.627750  0.506966  0.492516  0.471431  0.466299   
2     2023-10-31 02:05:00  0.494219  0.556344  0.486816  0.471571  0.451662   
3     2023-10-31 02:10:00  0.484080  0.510886  0.544255  0.471969  0.458980   
4     2023-10-31 02:15:00  0.488413  0.479148  0.495226  0.530544  0.456419   
...                   ...       ...       ...       ...       ...       ...   
17529 2023-12-30 22:40:00  0.710021  0.603074  0.500953  0.403712  0.322118   
17530 2023-12-30 22:45:00  0.710121  0.554092  0.476755  0.386994  0.289344   
17531 2023-12-30 22:50:00  0.817651  0.561233  0.457934  0.391904  0.298683   
17532 2023-12-30 22:55:00  0.699329  0.622970  0.460120  0.364878  0.297988   
17533 2023-12-30 23:00:00  0.679613  0.583150  0.522981  0.371006  0.274669   

          yhat5     yhat6     yhat7     yhat8  ...      ar11      ar12  \
0      0.509680  0.527672  0.463352  0.443624  ...  1.209572  1.267414   
1      0.476846  0.501996  0.522233  0.454197  ...  1.172527  1.247805   
2      0.451778  0.455442  0.481494  0.504956  ...  1.117382  1.165857   
3      0.444255  0.437518  0.442595  0.475114  ...  1.097758  1.104801   
4      0.450292  0.429699  0.423145  0.435136  ...  1.114358  1.100633   
...         ...       ...       ...       ...  ...       ...       ...   
17529  0.280500  0.168527  0.080431  0.009148  ...  6.379824  6.238949   
17530  0.238633  0.159381  0.055980 -0.017704  ...  6.408733  6.359982   
17531  0.233039  0.144627  0.071905 -0.019946  ...  6.423929  6.391564   
17532  0.236766  0.131642  0.049780 -0.005269  ...  6.474812  6.399544   
17533  0.237493  0.137272  0.041128 -0.022582  ...  6.520041  6.460826   

          trend  season_weekly  season_daily  future_regressors_additive  \
0      0.399356       1.389237     -2.268244                   -0.198594   
1      0.399260       1.391171     -2.271541                   -0.196666   
2      0.399162       1.395772     -2.286761                   -0.195702   
3      0.399066       1.397094     -2.286235                   -0.194738   
4      0.398968       1.399507     -2.299546                   -0.193774   
...         ...            ...           ...                         ...   
17529 -1.298330      -2.348764     -1.253359                   -1.687088   
17530 -1.298428      -2.347269     -1.336374                   -1.674555   
17531 -1.298523      -2.344958     -1.394196                   -1.661058   
17532 -1.298621      -2.343334     -1.453064                   -1.647562   
17533 -1.298719      -2.342131     -1.510233                   -1.634065   

       future_regressor_Incep  future_regressor_Tncep  \
0                         0.0               -0.198594   
1                         0.0               -0.196666   
2                         0.0               -0.195702   
3                         0.0               -0.194738   
4                         0.0               -0.193774   
...                       ...                     ...   
17529                     0.0               -1.687088   
17530                     0.0               -1.674555   
17531                     0.0               -1.661058   
17532                     0.0               -1.647562   
17533                     0.0               -1.634065   

       future_regressor_lab_day  future_regressor_lab_hour  
0                           0.0                        0.0  
1                           0.0                        0.0  
2                           0.0                        0.0  
3                           0.0                        0.0  
4                           0.0                        0.0  
...                         ...                        ...  
17529                       0.0                        0.0  
17530                       0.0                        0.0  
17531                       0.0       

## whole error

In [ ]:
K = 12 # number of step ahead
error_df = pd.DataFrame()
norm_factor = forecast['y'].max() - forecast['y'].min()
#get e = y_true - y_pred
for i in range(K) :
  error_df[f'e{i+1}'] =  forecast['y'] - forecast[f'yhat{i+1}']

error_df

e1        e2        e3        e4        e5        e6        e7  \
0      0.020011  0.043890  0.043422  0.036786  0.004856 -0.013136  0.051183   
1      0.120784  0.135235  0.156319  0.161451  0.150904  0.125754  0.105518   
2     -0.062125  0.007403  0.022649  0.042557  0.042441  0.038778  0.012725   
3     -0.026806 -0.060176  0.012110  0.025100  0.039825  0.046562  0.041484   
4      0.009265 -0.006813 -0.042132  0.031994  0.038120  0.058713  0.065268   
...         ...       ...       ...       ...       ...       ...       ...   
17529  0.106946  0.209068  0.306309  0.387902  0.429521  0.541494  0.629589   
17530  0.156029  0.233366  0.323127  0.420777  0.471488  0.550740  0.654141   
17531  0.256418  0.359717  0.425747  0.518968  0.584612  0.673024  0.745747   
17532  0.076359  0.239209  0.334451  0.401341  0.462563  0.567687  0.649549   
17533  0.096463  0.156632  0.308607  0.404944  0.442120  0.542341  0.638485   

             e8        e9       e10       e11       e12  
0      0.070911  0.064741 -0.017022 -0.016792 -0.074634  
1      0.173554  0.192289  0.188535  0.133000  0.057721  
2     -0.010737  0.058367  0.080061  0.064367  0.015892  
3      0.008966 -0.008072  0.046370  0.071135  0.064092  
4      0.053276  0.029622  0.006973  0.068900  0.082625  
...         ...       ...       ...       ...       ...  
17529  0.700873  0.811671  0.858423  0.917738  1.058612  
17530  0.727825  0.824349  0.903797  0.958015  1.006766  
17531  0.837597  0.930832  1.010927  1.092457  1.124822  
17532  0.704597  0.817151  0.895497  0.967097  1.042366  
17533  0.702195  0.783446  0.863651  0.944720  1.003935  

[17534 rows x 12 columns]

In [ ]:
normalize_mape = np.abs(error_df.div(forecast['y'],axis=0))

In [ ]:
# MAE
MAE = np.mean(np.abs(error_df),axis=0)
# RMSE
RMSE = np.sqrt( np.mean(error_df**2,axis=0))
# MAPE
MAPE = np.mean(np.abs(error_df.div(forecast['y'],axis=0)), axis=0)*100
# MBE
MBE = np.mean(error_df,axis=0)
# minmax NMAE
NMAE =  np.mean(np.abs(error_df),axis=0)/norm_factor
error_table = pd.DataFrame({'step':range(1,K+1),'MAE':MAE,'RMSE':RMSE,'MAPE':MAPE,'MBE':MBE,'NMAE':NMAE})
error_table


step       MAE      RMSE       MAPE       MBE      NMAE
e1      1  0.425614  0.719119  15.886537  0.038761  0.020536
e2      2  0.485758  0.841173  19.358841  0.069076  0.023438
e3      3  0.560325  0.939177  23.471503  0.093879  0.027036
e4      4  0.621924  1.001780  27.677478  0.119711  0.030008
e5      5  0.661827  1.039126  30.856005  0.127632  0.031934
e6      6  0.710671  1.090602  34.269434  0.158790  0.034290
e7      7  0.766589  1.154711  37.614820  0.184868  0.036988
e8      8  0.829900  1.229858  41.107975  0.201539  0.040043
e9      9  0.879320  1.285933  44.295775  0.232040  0.042428
e10    10  0.918677  1.323621  47.017804  0.250554  0.044327
e11    11  0.949463  1.352513  49.645589  0.270717  0.045812
e12    12  0.982781  1.387232  52.105558  0.281320  0.047420

## Error by hour

In [ ]:

df_eval = forecast[['ds',    'y'] + [ f'yhat{i+1}' for i in range(K)]]
error_df = pd.DataFrame()
error_df['ds'] = df_eval['ds']
error_df['y'] = df_eval['y']
#get e = y_true - y_pred
for i in range(K) :
  error_df[f'e{i+1}'] =  forecast['y'] - forecast[f'yhat{i+1}']

error_df

ds         y        e1        e2        e3        e4  \
0     2023-10-31 01:55:00  0.514536  0.020011  0.043890  0.043422  0.036786   
1     2023-10-31 02:00:00  0.627750  0.120784  0.135235  0.156319  0.161451   
2     2023-10-31 02:05:00  0.494219 -0.062125  0.007403  0.022649  0.042557   
3     2023-10-31 02:10:00  0.484080 -0.026806 -0.060176  0.012110  0.025100   
4     2023-10-31 02:15:00  0.488413  0.009265 -0.006813 -0.042132  0.031994   
...                   ...       ...       ...       ...       ...       ...   
17529 2023-12-30 22:40:00  0.710021  0.106946  0.209068  0.306309  0.387902   
17530 2023-12-30 22:45:00  0.710121  0.156029  0.233366  0.323127  0.420777   
17531 2023-12-30 22:50:00  0.817651  0.256418  0.359717  0.425747  0.518968   
17532 2023-12-30 22:55:00  0.699329  0.076359  0.239209  0.334451  0.401341   
17533 2023-12-30 23:00:00  0.679613  0.096463  0.156632  0.308607  0.404944   

             e5        e6        e7        e8        e9       e10       e11  \
0      0.004856 -0.013136  0.051183  0.070911  0.064741 -0.017022 -0.016792   
1      0.150904  0.125754  0.105518  0.173554  0.192289  0.188535  0.133000   
2      0.042441  0.038778  0.012725 -0.010737  0.058367  0.080061  0.064367   
3      0.039825  0.046562  0.041484  0.008966 -0.008072  0.046370  0.071135   
4      0.038120  0.058713  0.065268  0.053276  0.029622  0.006973  0.068900   
...         ...       ...       ...       ...       ...       ...       ...   
17529  0.429521  0.541494  0.629589  0.700873  0.811671  0.858423  0.917738   
17530  0.471488  0.550740  0.654141  0.727825  0.824349  0.903797  0.958015   
17531  0.584612  0.673024  0.745747  0.837597  0.930832  1.010927  1.092457   
17532  0.462563  0.567687  0.649549  0.704597  0.817151  0.895497  0.967097   
17533  0.442120  0.542341  0.638485  0.702195  0.783446  0.863651  0.944720   

            e12  
0     -0.074634  
1      0.057721  
2      0.015892  
3      0.064092  
4      0.082625  
...         ...  
17529  1.058612  
17530  1.006766  
17531  1.124822  
17532  1.042366  
17533  1.003935  

[17534 rows x 14 columns]

In [ ]:

ds_hour = pd.DataFrame({'hour of target':[f'{hour:02}:00' for hour in range(24)]})
# calculate metric by hour
# iterate over hour
MAE = []
RMSE = []
MAPE = []
MBE = []
NMAE = []
for hour in range(24) :
  hour_df = error_df[error_df['ds'].dt.hour == hour][[f'e{k+1}'  for k in range(K)]]
  y = error_df[error_df['ds'].dt.hour == hour]['y']
  print
  norm_factor = y.max() - y.min()
  # MAE
  MAE.append( np.mean(np.abs(hour_df),axis=0))
  # RMSE
  RMSE.append(np.sqrt( np.mean(hour_df**2,axis=0)) )
  # MAPE
  MAPE.append( np.mean(np.abs(hour_df.div(y,axis=0)), axis=0)*100 )
  # MBE
  MBE.append(np.mean(hour_df,axis=0) )
  # minmax NMAE
  NMAE.append ( np.mean(np.abs(hour_df),axis=0)/norm_factor)
MAE = pd.DataFrame(MAE)
RMSE = pd.DataFrame(RMSE)
MAPE = pd.DataFrame(MAPE)
MBE = pd.DataFrame(MBE)
NMAE = pd.DataFrame(NMAE)
MAE['hour of target'] = ds_hour
RMSE['hour of target'] = ds_hour
MAPE['hour of target'] = ds_hour
MBE['hour of target'] = ds_hour
NMAE['hour of target'] = ds_hour




In [ ]:
import plotly.graph_objects as go

# Assuming mae_hour_df is your DataFrame
step = [1,3,6,12]
fig = go.Figure()
metric = 'MAPE'
for k in step:
    fig.add_trace(go.Bar(x=MAPE['hour of target'], y=MAPE[f'e{k}'], name=str(k*5) +'min ahead' ))

fig.update_layout(
    title=metric + ' of predicted load by hour',
    xaxis_title='Hour',
    yaxis_title=metric + ' (%) ',
    barmode='group',
    width=2480,
    height=1000,
    font = {'size' : 24},
    plot_bgcolor='white',
    xaxis=dict(
        linecolor='black',
        showgrid=True,
        gridcolor='black'
    ),
    yaxis=dict(
        linecolor='black',
        showgrid=True,
        gridcolor='black'
    )
)

fig.show()

In [ ]:
import numpy as np
import pandas as pd
from sklearn.metrics import mean_absolute_error, mean_squared_error
import plotly.graph_objects as go

# Assuming result_df is your DataFrame

# Create Plotly time series plot
ts_fig = go.Figure()
step = [1,3,6,12]
ts_fig.add_trace(go.Scatter(x=df_eval['ds'], y=df_eval['y'], name='Actual', mode='lines',line=dict(color='#000000')))
for k in step :
  ts_fig.add_trace(go.Scatter(x=df_eval['ds'], y=df_eval[f'yhat{k}'], name=str(k*5) +' min ahead', mode='lines'))

ts_fig.update_layout(
                  title='Predicted and actual load consumption',
                  xaxis_title='Datetime',
                  yaxis_title='Ptot (kW)',
                  width=2480,
                  height=1000,
                  font = {'size' : 24},
                  plot_bgcolor='white',
                  xaxis=dict(
                      linecolor='black',
                      showgrid=True,
                      gridcolor='black'
                  ),
                  yaxis=dict(
                      linecolor='black',
                      showgrid=True,
                      gridcolor='black'
                  )
)


ts_fig.show()

In [ ]:
ts_fig = go.Figure()

ts_fig.add_trace(go.Scatter(x=forecast['ds'], y=forecast['season_daily'], name='daily_seasonality', mode='lines'))
ts_fig.add_trace(go.Scatter(x=forecast['ds'], y=forecast['season_weekly'], name='weekly_seasonality', mode='lines'))
ts_fig.add_trace(go.Scatter(x=forecast['ds'], y=forecast['trend'], name='trend', mode='lines'))

ts_fig.update_layout(title='Seasonality and trend component decompose by NeuralProphet',
                  xaxis_title='Datetime',
                  yaxis_title='Power (kW)',
                  width=2480,
                  height=1000,
                  font = {'size' : 24},
                  plot_bgcolor='white',
                  xaxis=dict(
                      linecolor='black',
                      showgrid=True,
                      gridcolor='black'
                  ),
                  yaxis=dict(
                      linecolor='black',
                      showgrid=True,
                      gridcolor='black'
                  )
                     )

ts_fig.show()